In [20]:
# 04_extract_values.ipynb

import os
import pandas as pd
import json

# Define the directory containing the data
data_dir = '../data/entities'

# Ensure the data directory exists
os.makedirs(data_dir, exist_ok=True)

# Load the JSON configuration
config_path = '../config.json'
with open(config_path, 'r') as config_file:
    config = json.load(config_file)

# Function to handle potential negative values
def handle_negative_value(value):
    if isinstance(value, str) and value.startswith('('):
        return '-' + value.strip('(').rstrip(')')
    return value

# Function to extract the required value from the specified column
def extract_value(df, line_name, column_idx, occurrence=-1, entity_name='', form_type=''):
    try:
        matching_rows = [row for i, row in df.iterrows() if line_name in row.to_string()]
        print(f"Entity: {entity_name}, Form: {form_type}, Line: '{line_name}'")
        print(f"Matching rows for '{line_name}': {matching_rows}")
        if not matching_rows:
            return 0

        row = matching_rows[occurrence]
        value = row.iloc[column_idx]
        print(f"Extracted value before handling negative for '{line_name}': {value}")
        return handle_negative_value(value)
    except Exception as e:
        print(f"Error extracting value for '{line_name}' in Entity '{entity_name}', Form '{form_type}': {e}")
        return 0

# Function to extract the value embedded within the text in the same cell
def extract_embedded_value(df, line_name, after_sequence, entity_name='', form_type=''):
    try:
        matching_rows = [row for i, row in df.iterrows() if line_name in row.to_string()]
        print(f"Entity: {entity_name}, Form: {form_type}, Line: '{line_name}'")
        print(f"Matching rows for embedded value '{line_name}': {matching_rows}")
        if matching_rows:
            text = matching_rows[-1][0]
            if line_name in text:
                parts = text.split(after_sequence)
                if len(parts) > 1:
                    embedded_value = parts[1].split()[0].strip()
                    print(f"Extracted embedded value for '{line_name}': {embedded_value}")
                    return embedded_value
        return 0
    except Exception as e:
        print(f"Error extracting embedded value for '{line_name}' in Entity '{entity_name}', Form '{form_type}': {e}")
        return 0

# Initialize an empty list to store the extracted data
data_list = []
form_type_list = []

# Initialize a list to store column names as per config order
ordered_columns = ['Entity']

# Walk through the data directory to find the relevant files
for root, dirs, files in os.walk(data_dir):
    for file in files:
        if file.endswith('.csv'):
            entity_name = os.path.basename(os.path.dirname(os.path.dirname(root)))
            form_type = os.path.basename(os.path.dirname(root))
            data = {'Entity': entity_name}

            print(f"Processing Entity: {entity_name}, Form: {form_type}, File: {file}")

            # Check if the form type exists in the config
            if form_type in config and file in config[form_type]:
                file_path = os.path.join(root, file)
                df = pd.read_csv(file_path)

                for item in config[form_type][file]:
                    line_name = item["line_name"]
                    column_name = item["column_name"]
                    extract_method = item["extract_method"]

                    if extract_method == "extract_value":
                        column_idx = item.get("column_idx", 0)
                        occurrence = item.get("occurrence", -1)
                        value = extract_value(df, line_name, column_idx, occurrence, entity_name, form_type)
                    elif extract_method == "extract_embedded_value":
                        after_sequence = item.get("after_sequence", "")
                        value = extract_embedded_value(df, line_name, after_sequence, entity_name, form_type)

                    data[column_name] = value
                    print(f"Extracted data for '{column_name}': {value}")
                    if column_name not in ordered_columns:
                        ordered_columns.append(column_name)

                form_type_list.append(form_type)

            if entity_name not in [d['Entity'] for d in data_list]:
                data_list.append(data)
            else:
                for d in data_list:
                    if d['Entity'] == entity_name:
                        d.update(data)

# Create a DataFrame from the extracted data
if data_list:
    df_all_values = pd.DataFrame(data_list)
    
    # Ensure the DataFrame columns are ordered as per the JSON config
    df_all_values = df_all_values[ordered_columns]
    
    # Sort the DataFrame by the 'Entity' column
    df_all_values = df_all_values.sort_values(by='Entity')
    
    # Print the DataFrame to check the extracted values
    print(df_all_values)

    # Determine the output file path based on form type
    unique_form_types = set(form_type_list)
    if len(unique_form_types) == 1:
        form_type = unique_form_types.pop()
    else:
        form_type = 'multiple_forms'
        
    output_file_path = f'../data/{form_type}_extracted_data.csv'
    df_all_values.to_csv(output_file_path, index=False)

    print(f"Extracted data has been saved to '{output_file_path}'")
else:
    print("No data extracted. The data list is empty.")


Processing Entity: Masterworks 091, LLC, Form: 1-SA, File: Consolidated_Balance_Sheet.csv
Processing Entity: Masterworks 091, LLC, Form: 1-SA, File: Consolidated_Statement_of_Members’_Equity.csv
Processing Entity: Masterworks 091, LLC, Form: 1-SA, File: Consolidated_Statement_of_Cash_Flows.csv
Processing Entity: Masterworks 091, LLC, Form: 1-SA, File: Consolidated_Statement_of_Operations.csv
Processing Entity: Masterworks 091, LLC, Form: 1-K, File: Consolidated_Balance_Sheet.csv
Processing Entity: Masterworks 091, LLC, Form: 1-K, File: Consolidated_Statement_of_Members’_Equity.csv
Processing Entity: Masterworks 091, LLC, Form: 1-K, File: Consolidated_Statement_of_Cash_Flows.csv
Processing Entity: Masterworks 091, LLC, Form: 1-K, File: Consolidated_Statement_of_Operations.csv
Processing Entity: Masterworks 212, LLC, Form: 1-SA, File: Consolidated_Balance_Sheet.csv
Processing Entity: Masterworks 212, LLC, Form: 1-SA, File: Consolidated_Statement_of_Members’_Equity.csv
Processing Entity: 

In [27]:
# 04_extract_values.ipynb

import os
import pandas as pd
import json

# Define the directory containing the data
data_dir = '../data/entities'

# Ensure the data directory exists
os.makedirs(data_dir, exist_ok=True)

# Load the JSON configuration
config_path = '../config.json'
with open(config_path, 'r') as config_file:
    config = json.load(config_file)

# Function to handle potential negative values
def handle_negative_value(value):
    if isinstance(value, str) and value.startswith('('):
        return '-' + value.strip('(').rstrip(')')
    return value

# Function to extract the required value from the specified column
def extract_value(df, line_name, column_idx, occurrence=0, entity_name='', form_type=''):
    try:
        matching_rows = [row for i, row in df.iterrows() if line_name in row.to_string()]
        print(f"Entity: {entity_name}, Form: {form_type}, Line: '{line_name}'")
        print(f"Matching rows for '{line_name}': {matching_rows}")
        if not matching_rows:
            return 0

        row = matching_rows[occurrence]
        value = row.iloc[column_idx]
        print(f"Extracted value before handling negative for '{line_name}': {value}")
        return handle_negative_value(value)
    except Exception as e:
        print(f"Error extracting value for '{line_name}' in Entity '{entity_name}', Form '{form_type}': {e}")
        return 0

# Function to extract the value embedded within the text in the same cell
def extract_embedded_value(df, line_name, after_sequence, entity_name='', form_type=''):
    try:
        matching_rows = [row for i, row in df.iterrows() if line_name in row.to_string()]
        print(f"Entity: {entity_name}, Form: {form_type}, Line: '{line_name}'")
        print(f"Matching rows for embedded value '{line_name}': {matching_rows}")
        if matching_rows:
            text = matching_rows[-1][0]
            if line_name in text:
                parts = text.split(after_sequence)
                if len(parts) > 1:
                    embedded_value = parts[1].split()[0].strip()
                    print(f"Extracted embedded value for '{line_name}': {embedded_value}")
                    return embedded_value
        return 0
    except Exception as e:
        print(f"Error extracting embedded value for '{line_name}' in Entity '{entity_name}', Form '{form_type}': {e}")
        return 0

# Initialize an empty dictionary to store the extracted data in a pivot format
data_dict = {}

# Walk through the data directory to find the relevant files
for root, dirs, files in os.walk(data_dir):
    for file in files:
        if file.endswith('.csv'):
            entity_name = os.path.basename(os.path.dirname(os.path.dirname(root)))
            form_type = os.path.basename(os.path.dirname(root))

            print(f"Processing Entity: {entity_name}, Form: {form_type}, File: {file}")

            # Check if the form type exists in the config
            if form_type in config and file in config[form_type]:
                file_path = os.path.join(root, file)
                df = pd.read_csv(file_path)

                for item in config[form_type][file]:
                    line_name = item["line_name"]
                    column_name = item["column_name"]
                    extract_method = item["extract_method"]

                    if extract_method == "extract_value":
                        column_idx = item.get("column_idx", 0)
                        occurrence = item.get("occurrence", 0)
                        value = extract_value(df, line_name, column_idx, occurrence, entity_name, form_type)
                    elif extract_method == "extract_embedded_value":
                        after_sequence = item.get("after_sequence", "")
                        value = extract_embedded_value(df, line_name, after_sequence, entity_name, form_type)

                    if column_name not in data_dict:
                        data_dict[column_name] = {}
                    data_dict[column_name][entity_name] = value
                    print(f"Extracted data for '{column_name}': {value}")

# Convert the dictionary to a DataFrame
df_all_values = pd.DataFrame(data_dict).T

# Ensure rows are ordered as per the JSON config
row_order = [item["column_name"] for item in config["1-SA"]["Consolidated_Statement_of_Cash_Flows.csv"]]
df_all_values = df_all_values.reindex(row_order)

# Ensure columns are ordered by entity name
column_order = sorted(df_all_values.columns)
df_all_values = df_all_values[column_order]

# Print the DataFrame to check the extracted values
print(df_all_values)

# Determine the output file path based on form type
output_file_path = '../data/1-SA_extracted_data.csv'
df_all_values.to_csv(output_file_path)

print(f"Extracted data has been saved to '{output_file_path}'")


Processing Entity: Masterworks 091, LLC, Form: 1-SA, File: Consolidated_Balance_Sheet.csv
Processing Entity: Masterworks 091, LLC, Form: 1-SA, File: Consolidated_Statement_of_Members’_Equity.csv
Processing Entity: Masterworks 091, LLC, Form: 1-SA, File: Consolidated_Statement_of_Cash_Flows.csv
Entity: Masterworks 091, LLC, Form: 1-SA, Line: 'Cash Flows from Operating Activities'
Matching rows for 'Cash Flows from Operating Activities': [Unnamed: 0                                           Cash Flows from Operating Activities:
Unnamed: 1                                                                             NaN
For the PeriodJanuary 1, 2023Through June 30,2023                                      NaN
Unnamed: 3                                                                             NaN
Unnamed: 4                                                                             NaN
For the PeriodJanuary 1, 2022Through June 30,2022                                      NaN
Unnamed: 6   